In [193]:
import codecs
import sys
import urllib.request
import bs4
import os
import time
import re
from selenium import webdriver

In [194]:
#URL
LIST_URL = 'https://psnprofiles.com/leaderboard/all?page='
MAIN_URL = 'https://psnprofiles.com'

In [195]:
#ディレクトリ名
GAME_PATH = '../../psn_game'
USER_PATH = GAME_PATH + '/user' 
DATA_PATH = GAME_PATH + '/data'

In [196]:
#重くなるから平均だけとる
game_trofy = []
#出現回数
game_count = []
#ユーザ名リスト
user_id_list = []
#ゲームURL
game_urls = []
#game_information=[['game_url',image_url',['ps4','ps3','vita']]]
game_information = []

In [197]:
filename_games = DATA_PATH + '/games.txt'
filename_games2 = DATA_PATH + '/games+.txt'
filename_images = DATA_PATH + '/images.txt'
filename_platform = DATA_PATH + '/platform.txt'
filename_average = DATA_PATH + '/average.txt'
filename_count = DATA_PATH + '/count.txt'
filename_game_url = DATA_PATH + '/games_url.txt'
filename_users = DATA_PATH + '/users.txt'

In [198]:
#重くなるから平均だけとる
game_trofy = []
#出現回数
game_count = []
#ユーザ名リスト
user_id_list = []
#ゲームURL
game_urls = []
#game_information=[['game_url',image_url',['ps4','ps3','vita']]]
game_information = []
#読み出し
f = open(filename_average,"r")
for x in f:
    game_trofy.append(x.rstrip("\n"))
f.close()

f = open(filename_count,"r")
for x in f:
    game_count.append(int(x.rstrip("\n")))
f.close()

f = open(filename_users,"r")
for x in f:
    user_id_list.append(x.rstrip("\n"))
f.close()

f = open(filename_game_url,'r')
for x in f:
    game_urls.append(x.rstrip("\n"))
    
f1 = open(filename_games2, 'r')
f2 = open(filename_images, 'r')
f3 = open(filename_platform, 'r')
for (i,j,k) in zip(f1,f2,f3):
    li = []
    li.append(i.strip('\n'))
    li.append(j.strip('\n'))
    l = []
    l.append(int(k[0]))
    l.append(int(k[2]))
    l.append(int(k[4]))
    li.append(l)
    game_information.append(li)

In [199]:
#ページをクロール
def get_userlist(start, pages):
    #ユーザをリストに
    id_list = []
    for i in range(start, start+pages):
        #leaderboadから取得する
        list_url = LIST_URL + str(i)
        try:
            page_html = urllib.request.urlopen(list_url).read()
        except Exception as e:
                estr = str(i) + " is 404"
                print(estr)
                continue
        soup = bs4.BeautifulSoup(page_html,'lxml')
        table = soup.find('table', id ='leaderboard')
        user_list = table.find_all('a', class_ = 'title')
        for href in user_list:
            id = href.get('href')
            #既にとったIDならリストに加えない
            if user_id_list.count(id.strip('/'))==0:
                #ユーザをリストに加える
                id_list.append(id)
    return id_list

In [200]:
#ページスクロール soupを返す
def get_page_scroll(url):
    #PhantomJs
    #https://gist.github.com/julionc/7476620
    driver = webdriver.PhantomJS()
    driver.get(url)
    #スクロールダウン
    #スクロールされてるか判断する部分
    lastHeight = driver.execute_script("return document.body.scrollHeight")
    soup = []
    while True:
        #スクロールダウン
        driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")  
        #読み込まれるのを待つ
        time.sleep(5)
        newHeight = driver.execute_script("return document.body.scrollHeight")
        page_html = driver.page_source.encode('utf-8')
        soup = bs4.BeautifulSoup(page_html,'lxml')
        #スクロールされてるか判断する部分
        if newHeight == lastHeight:
            break
        lastHeight = newHeight
    return soup

In [201]:
#平均トロフィー取得率取得
def get_average_trofy(arg):
    try:
        url = MAIN_URL+arg
        print(url)
        regex = r'[^\x00-\x7F]'
        matchedList = re.findall(regex,url)
        for m in matchedList:
            url = url.replace(m, urllib.parse.quote_plus(m, encoding="utf-8"))
        game_urls.append(url)
        soup=bs4.BeautifulSoup(urllib.request.urlopen(url).read(),'lxml')
    except Exception as e:
        estr=str(arg)+" is 404"
        print(estr)
        return
    stats = soup.find('div', attrs = {'class':'stats flex'}).get_text()
    tmp = re.findall(r'\d\d?%Average Completion',stats)
    str = tmp[0].replace('%Average Completion','')
    game_trofy.append(str)

In [202]:
#game_information=[['game_url',image_url',['ps4','ps3','vita']]]
#game_information = []
#game_trofy=[owners,recent players, platinum achievers, average, earned]
#重くなるから平均だけとる
#game_trofy = []
#get_info('/mmilkkr', GAME_PATH + '/mmilkkr.txt')
#print(game_trofy)

In [203]:
#ユーザの情報取得
def get_info(id, filename):
    #ユーザ名を1行めに書き込む
    f = open(filename, 'w')
    #ユーザ情報
    user_list = []
    #URL
    url = MAIN_URL + id 
    soup = get_page_scroll(url)
    #ゲーム画像とゲーム名
    #tableタグ取得
    Table = soup.find('table', attrs={'class':'zebra', 'id':'gamesTable'})
    if Table==None:
        print('private user')
        return -1
    user_id_list.append(id.strip('/'))
    #トロフィー平均取得率を得るためのゲームURL
    Game = Table.find_all('div', attrs={'class':'ellipsis'})
    #pictureタグ取得
    PIC = Table.find_all('picture', attrs={'class':'game'})
    #ユーザトロフィー取得率
    TOR = Table.find_all('div', attrs={'class':'progress-bar'})
    #プラットフォーム取得
    PLA = Table.find_all('div', attrs={'class':'platforms'})
    for (i,pic) in enumerate(PIC):
        LIST = []
        #imgタグ取得
        IMG = pic.find('img')
        #ゲームURL
        #game_name=Game[i].get_text().replace('\n','').replace('\t','').replace('•', '・')
        game_url = Game[i].a.get('href').replace(id,'')
        #print(MAIN_URL+'/'+game_url)
        #ゲームの追加
        LIST.append(game_url)
        #ゲーム画像URL追加
        try:
            LIST.append(IMG['src'])
        except:
            print(id,' image url none:')
            None
        #プラットフォーム取得
        try:
            Pla = [0,0,0]
            for pla in PLA[i].find_all('span'):
                if 'PS4' in pla:
                    Pla[0]=1
                elif 'PS3' in pla:
                    Pla[1]=1
                elif 'Vita' in pla:
                    Pla[2]=1
                else:
                    pass
            LIST.append(Pla)
        except:
            print(id,' platform none:')
            None
        if user_list.count(LIST)==0:
            user_list.append(LIST)
        #まだ取得していなゲームなら追加
        if game_information.count(LIST)==0:
            #平均トロフィー取得率取得
            get_average_trofy(game_url)
            game_information.append(LIST)
            index = game_information.index(LIST)
            game_count.append(1)
            print(index, game_count[index])
        else:
            index = game_information.index(LIST)
            game_count[index]=game_count[index]+1
            print(index, game_count[index])
    #ユーザトロフィー
    for (i,list) in enumerate(user_list):
        tor = TOR[i].find('span').get_text().strip('%')
        f.write(str(game_information.index(list))+'\t'+tor+'\n')

In [204]:
if __name__ == '__main__':
    CURRENT = 2000
    try:
        os.makedirs(USER_PATH)
        os.makedirs(DATA_PATH)
    except FileExistsError:
        pass
    #ページ指定
    #start_pages=[100]
    start_pages=[1000,2000,3000,10000,15000,17000,20000,30000]
    #何人ずつ得るか
    #number_of_users=[2]
    number_of_users = [250,250,250,250,250,250,250,250]
    #合計人数
    all_number_of_user = 0
    for i in number_of_users:
         all_number_of_user = all_number_of_user + i
    j=0
    for (start, number) in zip(start_pages,number_of_users):
        #leaderboad,1ページ辺り50人得られる 第二引数10で500人
        id_list = get_userlist(start, 20)
        i=0
        for id in id_list:
            print(MAIN_URL+id)
            usercount = i+number*j+CURRENT
            fname = USER_PATH + '/' + str(usercount) + '.txt'
            #ユーザ情報が非公開ならインクリメントしない
            if get_info(id, fname) == -1:
                i=i-1
            i=i+1
            if i == number:
                break
        j = j+1
    print('ゲーム数:\t',len(game_information),'\tユーザ数:', all_number_of_user+CURRENT)

https://psnprofiles.com/tornmethos
876 288
513 557
529 169
2691 43
866 175
537 112
562 227
889 463
574 320
552 444
1243 128
670 282
554 275
564 283
89 342
886 218
1146 90
896 273
558 472
1466 171
1084 231
855 208
367 297
591 246
488 205
1274 59
1083 254
489 412
1089 315
1078 138
181 693
443 180
665 439
618 388
2319 83
901 167
481 594
622 384
629 519
1202 140
1100 461
643 509
1246 104
648 275
655 526
702 221
653 391
1110 273
664 321
1200 235
671 263
899 568
942 251
693 257
580 205
573 257
210 358
674 480
707 275
680 658
713 231
727 312
1415 222
715 147
717 333
733 335
1203 99
730 473
731 416
531 662
754 244
299 777
157 884
2220 15
95 286
829 645
771 332
950 371
68 179
833 981
188 188
3084 4
357 767
117 880
2236 57
64 325
381 251
257 330
48 503
969 926
1360 31
402 881
176 556
413 175
1189 102
237 403
292 158
1115 148
985 227
3022 58
921 153
358 733
1302 236
66 335
1116 178
1345 38
412 282
306 106
1388 30
786 1046
834 499
171 443
351 633
311 250
973 16
19 70
982 623
200 87
207 701
970 335

481 597
853 59
453 135
876 289
866 176
3411 2
1893 22
562 228
518 334
488 206
1075 211
849 31
859 96
530 257
496 206
583 449
1354 28
1266 135
500 306
2146 23
181 695
618 390
1482 107
542 157
1451 10
https://psnprofiles.com/trophies/4086-handball-16
4806 1
469 329
1095 122
1142 56
1480 22
559 112
569 167
537 114
528 44
547 116
462 295
443 181
1192 132
2027 11
554 276
2031 76
1806 46
1479 122
557 57
586 71
1399 59
2114 22
502 12
1514 36
572 165
1237 148
119 99
89 345
566 266
563 145
1621 20
595 72
1865 88
889 464
653 395
441 85
1090 182
513 561
1911 66
54 95
1149 124
423 127
236 278
183 98
790 179
237 406
235 85
670 284
3179 6
549 214
3070 8
886 219
643 513
644 142
591 247
589 354
1355 133
552 447
581 303
1485 168
631 171
470 309
636 126
897 257
1309 87
1520 57
1895 54
1091 195
1168 32
1246 105
3833 16
558 476
1522 38
911 170
880 188
544 479
472 112
1796 20
1085 279
615 241
879 60
1528 159
1202 142
564 284
671 265
655 530
717 335
654 299
635 218
2457 14
610 189
1280 121
1092 153
2009 33


512 57
1357 64
1092 154
868 34
1141 86
3248 31
https://psnprofiles.com/trophies/4078-brunswick-pro-bowling
4808 1
901 171
1098 185
1660 4
542 158
1075 212
857 45
539 36
572 167
1137 11
475 6
863 53
897 259
555 56
1100 463
1450 132
1685 18
1622 17
560 35
4001 8
896 276
2691 44
4159 4
566 269
1480 23
1276 37
1680 53
1481 64
181 697
576 133
470 310
490 259
581 305
486 239
589 356
1243 130
https://psnprofiles.com/trophies/4108-tiny-troopers-joint-ops-zombie-edition
4809 1
1895 55
2668 13
1436 53
1851 30
2556 55
618 393
577 58
889 465
1616 18
585 208
460 272
488 208
340 137
1097 257
617 17
2424 22
574 322
1445 52
2426 15
2307 14
444 190
887 46
1910 18
1163 76
590 235
443 184
639 125
662 191
717 339
731 421
629 525
673 69
663 154
625 94
1466 174
633 169
469 332
880 189
1811 82
1118 98
2150 8
1014 107
3837 17
3114 41
2153 14
649 247
726 497
588 384
564 286
670 287
613 325
4264 43
206 37
4407 11
118 35
212 107
936 141
106 76
2115 28
3543 17
207 707
231 449
990 170
281 21
714 167
680 666
1074 2

870 76
1141 87
469 333
1544 8
2059 12
723 445
518 335
1086 123
544 483
1454 4
2013 7
2973 8
3866 4
631 175
2317 4
1961 7
1092 155
1094 22
2434 19
1137 12
1084 235
1451 12
1142 57
1083 258
1443 6
1089 319
680 667
1308 22
1626 22
874 106
909 187
460 274
855 210
1818 161
618 395
583 454
1842 55
1085 281
622 390
695 111
490 261
470 312
653 398
891 56
1619 17
1729 21
1146 92
2048 3
655 534
671 268
611 3
3470 14
1091 200
1740 16
1366 101
1759 22
684 87
768 556
2117 2
642 9
692 90
676 15
584 138
514 56
677 54
2124 4
3806 17
1249 67
2205 14
2458 6
1255 39
226 92
1489 48
603 94
1607 53
607 51
659 231
661 129
686 39
1111 162
1184 58
688 69
766 371
3484 14
742 68
734 322
480 92
682 61
2076 18
218 106
286 259
609 84
1122 93
744 217
709 65
689 157
691 51
368 156
716 88
1769 47
718 147
720 126
1191 83
2284 69
1828 100
3066 4
1114 133
242 164
963 106
626 122
268 298
765 423
600 226
769 169
1824 93
1190 85
https://psnprofiles.com/lilsasi
899 576
358 743
88 94
11 233
847 24
308 602
215 683
702 226
469 

4824 1
https://psnprofiles.com/trophies/4231-マブラヴ
4825 1
319 335
1847 35
2861 6
3399 17
630 146
2560 24
3354 6
3325 7
3137 19
486 241
581 307
604 46
4317 2
3138 6
627 118
908 83
1844 31
911 173
2788 4
3139 32
743 110
3158 10
2695 37
3552 17
1101 134
3516 16
4723 3
3729 19
659 232
600 227
1899 45
2263 9
3291 26
3142 7
187 108
607 52
3341 16
1849 51
626 123
2348 13
3728 7
1202 146
2251 13
4322 5
932 176
4724 2
4069 3
3289 32
1249 68
740 127
4134 7
3361 21
3143 14
1991 36
3145 26
4133 9
2270 20
3316 17
2462 62
4325 3
3148 16
https://psnprofiles.com/trophies/1886-cure-mate-club
4826 1
https://psnprofiles.com/trophies/1957-プリンセスストライク
4827 1
3730 6
649 250
4328 3
1763 53
603 95
1781 50
2616 47
3351 2
1114 134
1834 78
4289 15
3203 11
751 161
3151 17
1120 170
2855 36
765 424
2275 15
209 225
368 157
1367 35
3156 25
3157 18
606 96
3154 34
216 280
3282 22
722 73
3781 9
1774 84
1842 56
4338 4
3737 6
1793 24
2797 18
3211 16
716 89
2796 5
3160 8
2829 28
3782 5
748 211
3784 13
3574 7
612 56
2809 37
3

...

866 333
488 411
726 1028
566 520
622 817
886 415
599 165
884 1306
73 2053
754 449
970 630
1019 509
837 2017
829 1225
142 1220
805 208
1002 193
793 537
215 1264
91 1893
3375 41
99 1674
1346 198
155 949
1058 317
https://psnprofiles.com/MrVonHutch
138 774
73 2054
1213 439
173 1988
754 450
352 896
822 1437
120 953
323 912
358 1360
91 1894
158 1951
76 325
837 2018
303 1122
157 1666
771 625
117 1677
970 631
969 1788
https://psnprofiles.com/aramansell
181 1391
527 650
536 246
518 654
598 75
583 883
530 549
544 931
643 1043
644 289
573 519
2308 165
531 1294
594 669
899 1150
202 456
821 689
920 456
1209 535
798 756
93 324
1182 233
308 1162
325 1238
358 1361
1926 177
139 766
390 835
273 1058
347 1121
261 1213
https://psnprofiles.com/likerone123
1363 162
877 275
1089 664
574 659
590 436
670 558
513 1104
566 521
500 644
469 637
844 181
580 424
1245 91
583 884
2498 23
629 1035
1110 526
613 606
531 1295
509 483
1466 355
610 375
481 1171
648 533
620 1044
884 1307
667 455
622 818
899 1151
209 430
181 

99 1681
299 1487
970 641
324 393
323 916
1360 52
91 1899
238 2076
381 490
105 223
1873 181
355 452
981 378
182 877
67 1689
117 1688
827 585
160 334
150 1158
402 1681
173 1993
785 440
207 1389
786 2031
969 1799
800 63
829 1234
262 721
799 113
315 402
290 792
418 494
22 1239
3457 19
281 47
833 1864
1388 66
392 427
386 842
956 190
328 202
403 207
1264 139
71 275
1053 130
1002 196
179 192
975 265
1010 1841
837 2025
793 546
996 752
810 209
https://psnprofiles.com/Skelly_83
697 664
781 577
1376 136
264 684
309 329
108 76
2662 47
201 233
996 753
205 236
121 207
390 836
981 379
1361 90
117 1689
254 1425
206 67
969 1800
991 329
73 2064
323 917
837 2026
367 539
139 770
786 2032
150 1159
1010 1842
2543 25
825 191
https://psnprofiles.com/kevlin
116 954
150 1160
985 459
386 843
37 385
829 1235
360 638
827 586
380 476
929 615
437 1208
67 1690
215 1267
35 599
207 1390
1010 1843
2090 274
1927 187
402 1682
792 546
171 879
253 98
155 954
1036 1098
https://psnprofiles.com/B_dOn88
574 661
1075 403
3248 70

358 1374
837 2032
367 540
265 283
6 866
1331 168
64 617
360 643
76 326
282 1730
1421 238
257 651
382 995
157 1674
91 1912
299 1490
1125 216
939 40
117 1698
131 116
777 187
3036 158
969 1815
782 293
290 797
390 840
158 1969
1334 62
238 2082
2938 159
120 958
1036 1107
1330 261
1023 223
786 2046
173 2000
1010 1858
825 192
https://psnprofiles.com/Dj_KiLl3r_101
8 533
135 709
357 1513
358 1375
238 2083
132 396
982 1192
969 1816
418 498
808 208
2781 60
303 1126
1922 146
402 1689
992 311
833 1876
373 441
397 1272
985 461
794 153
822 1444
1330 262
1396 216
52 192
432 188
786 2047
1225 418
1231 427
173 2001
158 1970
1010 1859
22 1246
https://psnprofiles.com/BringMeYourBones
2142 87
6 867
1135 95
49 67
936 261
244 497
1279 133
68 331
1341 300
981 381
62 630
282 1731
117 1699
786 2048
925 210
1873 183
367 541
799 117
215 1269
969 1817
2941 21
789 92
116 957
290 798
996 759
805 212
322 401
307 1066
1036 1108
2681 108
155 960
1010 1860
158 1971
https://psnprofiles.com/jelliuz
325 1246
282 1732
754 4

1093 193
2042 69
1806 113
3468 6
1309 165
1136 162
1914 102
1375 55
1367 74
1314 85
368 278
2154 42
1974 13
676 24
681 30
2163 54
1176 53
1783 156
126 593
2525 18
202 459
766 707
688 126
1607 99
1322 271
1970 27
720 235
1740 30
234 370
798 764
2081 23
1205 341
2050 111
734 617
747 255
691 88
1775 99
751 310
2085 30
769 340
287 774
248 647
816 133
1373 101
1111 331
966 38
1265 326
1951 33
2087 78
379 391
815 79
1255 84
318 545
746 331
768 1065
431 18
1294 52
2195 46
2552 58
755 623
437 1216
https://psnprofiles.com/cs01106
3141 17
1307 94
4112 8
2566 68
2814 46
3307 13
2821 6
2797 43
1834 164
2828 17
2810 22
2829 65
3785 46
2815 108
2248 24
4067 17
3308 52
2254 27
266 1032
3310 54
3316 34
1325 75
2574 114
3214 20
969 1826
282 1739
2823 11
4910 4
2818 14
1850 50
768 1066
720 236
2285 130
2855 63
2859 29
786 2060
2891 83
3403 38
3404 84
2872 44
4602 9
2878 34
2571 73
2894 40
2887 57
2577 77
2860 64
2101 221
3317 11
2582 103
437 1217
2576 56
2901 12
2903 9
960 169
https://psnprofiles.com/me

722 148
746 332
1035 995
1758 89
268 577
157 1683
273 1066
209 434
2072 168
745 267
766 708
765 818
422 753
256 395
351 1257
178 524
93 328
261 1222
421 538
289 145
135 715
109 699
339 379
1210 671
698 605
287 775
73 2085
291 276
298 326
311 497
319 670
299 1498
238 2094
950 725
282 1747
266 1035
317 349
257 653
331 279
376 271
427 276
1264 141
323 925
338 322
337 363
286 464
361 414
402 1703
348 280
397 1282
254 1437
340 249
352 906
390 846
260 331
316 480
158 1984
231 873
821 693
929 623
1529 251
357 1519
798 766
829 1252
396 573
https://psnprofiles.com/kiera2
160 337
306 212
53 36
182 881
89 673
331 280
4533 13
382 1004
1359 130
422 754
319 671
215 1276
234 373
35 607
950 726
437 1220
135 716
826 169
57 180
180 304
2115 53
661 229
4371 12
262 726
698 606
347 1128
125 98
307 1073
1064 112
171 885
136 187
157 1684
381 493
1023 226
233 232
120 966
3031 57
829 1253
2655 19
402 1704
329 729
266 1036
232 799
243 373
1346 203
1014 213
1035 996
99 1690
392 431
1033 338
801 704
https://psnpr

In [178]:
fgame = open(filename_games, 'w')
fgame2 = open(filename_games2, 'w')
fimage = open(filename_images, 'w')
fplatform = open(filename_platform, 'w')
faverage = open(filename_average, 'w')
for i in range(len(game_information)):
    tmp = re.sub(r'/trophies/\d*-','',game_information[i][0])
    fgame.write(tmp+'\n')
    fgame2.write(game_information[i][0]+"\n")
    fimage.write(game_information[i][1]+'\n')
    for j in range(0,3):
        fplatform.write(str(game_information[i][2][j])+'\t')
    fplatform.write('\n')
for i in range(len(game_trofy)):
    faverage.write(game_trofy[i]+'\n')
fgame.close()
fgame2.close()
fimage.close()
fplatform.close()
faverage.close()
#print(game_information)

In [179]:
fcount = open(filename_count, 'w')
fgame_url = open(filename_game_url, 'w')
fgame_users = open(filename_users, 'w')
for i in game_count:
    fcount.write(str(i)+'\n')
fcount.close()
for i in game_urls:
    fgame_url.write(str(i)+'\n')
fgame_url.close()
for i in user_id_list:
    fgame_users.write(str(i)+'\n')
fgame_users.close()

In [84]:
import pandas as pd
filename_all = GAME_PATH + '/all.csv'
df = pd.DataFrame(game_information)
df.to_csv(filename_all, index=False)

In [85]:
df = pd.read_csv(filename_all)
list1 = df.values.tolist()

In [180]:
get_info('/mmilkkr', DATA_PATH + '/mmilkkr.txt')

https://psnprofiles.com/trophies/6930-va-11-hall-a
4803 1
2791 5
518 331
1479 120
3716 6
1803 17
1525 25
3124 6
843 37
3126 8
1272 116
1528 157
1935 8
636 125
1157 31
1799 28
643 509
876 288
878 81
2767 9
723 440
527 319
505 133
909 185
547 116
469 328
1307 50
544 476
1155 113
1091 195
2283 46
1836 29
530 256
470 306
2000 39
1844 31
911 170
3158 10
1779 14
1466 171
627 116
583 447
1846 9
481 594
659 228
126 305
1078 138
3291 26
1089 315
3045 39
3149 13
3361 21
3148 16
3145 26
1818 160
1861 23
1763 53
693 257
3736 9
899 568
884 645
1834 77
3516 16
766 368
1778 28
3289 32
